In [1]:
import numpy as np
import sys
import os

module_path = os.path.abspath(os.path.join('..'))
if module_path not in sys.path:
    sys.path.append(module_path)

import sim.ap_field_ar as ap
import sim.far_field_ar as ff
import sim.tele_geo_ar as tg
import sim.pan_mod_ar as pm

from utility.conversion import sky_to_focal, flat_sqgrid_to_ticks, flat_sqgrid_to_2dgrid
from utility.plotting import scalar_field_plot

In [2]:
# create panel offsets randomly
save = 0
error_rms = 35
adj_1_A = np.random.randn(1092) * error_rms
adj_2_A = np.random.randn(1092) * error_rms
panel_model2 = pm.panel_model_from_adjuster_offsets(
    2, adj_2_A, 1, save
)  # Panel Model on M2
panel_model1 = pm.panel_model_from_adjuster_offsets(
    1, adj_1_A, 1, save
)  # Panel Model on M1

In [18]:
# ###################### define telescope geometry
freq = 101.28 # frequency of signal source [GHz]
wavelength = (30.0 / freq) * 0.01 # [m]
wavelength = wavelength * 1e3 # [mm]
k = 2 * np.pi / wavelength
# positions of the source and receiver feedhorns [mm]
P_source = np.array([0, -7200.0, 1e6]) # unit [mm]
P_rx = np.array([0, 209.920654, -1.36822040e-02]) # unit [mm]
# P_source = np.array([0, -7200.0, 1e12]) # unit [mm]
# P_rx = np.array([0, 0, 0])
st_th_fwhp = 30.0/180.0*np.pi 

tele_geo = tg.TelescopeGeometry()
tele_geo.N_scan = 100  # pixels in 1D of grid
tele_geo.de_ang = .5 / 60.0 * np.pi / 180.0  # Far-field angle increment, arcmin = 1/60 degree
# arcmin_to_rad = 1.0 / 60 * np.pi / 180.0
# tele_geo.de_ang = 60.0/tele_geo.N_scan / (252.0/60.0) * arcmin_to_rad   # angle increment of telescope scan [rad]

tele_geo.lambda_ = wavelength / 1e3 # [m]
tele_geo.k = 2 * np.pi / tele_geo.lambda_  # wavenumber [1/m]
# tele_geo.th_fwhp = 44 * np.pi / 180  # full width half power of source feed [rad]
[tele_geo.x_tow, tele_geo.y_tow, tele_geo.z_tow] = P_source/1e3
[tele_geo.rx_x, tele_geo.rx_y, tele_geo.rx_z] = P_rx/1e3

# Azimuth and Elevation center [rad]
tele_geo.az0 = 0.0
tele_geo.el0 = np.arctan(-tele_geo.y_tow / tele_geo.z_tow)
# tele_geo.el0 = 7.6/1e3
# tele_geo.el0 = 0.0

# arrays of pointing angles of rays
angle_size = 0.29
theta_a, theta_b, theta_N = -np.pi / 2 - angle_size, -np.pi / 2 + angle_size, 100
phi_a, phi_b, phi_N = np.pi / 2 - angle_size, np.pi / 2 + angle_size, 100
theta = np.linspace(theta_a, theta_b, theta_N)
phi = np.linspace(phi_a, phi_b, phi_N)

# get parameters from telescope geometry
tg_th_1, tg_th2, tg_z_ap = tele_geo.th_1, tele_geo.th2, tele_geo.z_ap
tg_th_fwhp, tg_F_2 = tele_geo.th_fwhp, tele_geo.F_2

In [24]:
# Perform ray-tracing and simulation
rxmirror = ap.ray_mirror_pts(P_rx, tg_th2, tg_F_2, theta, phi)
apout = ap.aperature_fields_from_panel_model(panel_model1, panel_model2, \
                                    P_rx, tg_th_1, tg_th2, tg_z_ap, tg_th_fwhp, \
                                    theta, phi, rxmirror
                                    )
farbeam = ff.far_field_sim(apout, tele_geo, None)

In [25]:
az = flat_sqgrid_to_ticks(farbeam[0]).real
el = flat_sqgrid_to_ticks(farbeam[1]).real
beam_sky = flat_sqgrid_to_2dgrid(farbeam[2])
beammain = beam_sky[int(tele_geo.N_scan), int(tele_geo.N_scan)]
beam_sky = beam_sky * np.conj(beammain)
beam_sky = beam_sky / np.max(np.abs(beam_sky)) # normalize the field

In [26]:
############# plot the field #######################################
x = el * 60.0 * 180.0 / np.pi # [arcmin] 
y = az * 60.0 * 180.0 / np.pi # [arcmin]
field = beam_sky
scalar_field_plot(x, y, field, title='Beam on sky', xlabel="el [arcmin]", ylabel="az [arcmin]")

In [27]:
############# plot the field #######################################
z_fp_tg, x_fp_tg = sky_to_focal(el-tele_geo.el0, az)
field = np.flipud(beam_sky)
scalar_field_plot(z_fp_tg, x_fp_tg, field, title='Beam on focal plane', xlabel="z [mm]", ylabel="x [mm]")